This notebook trains **fixed-weight** precipitation forecasts for a single station from hourly observations:

- **PoP**: probability of rain (RR1 ≥ 0.1 mm/h) for each lead hour `h=1..168`
- **Intensity**: conditional mean rain rate μ(RR1 | RR1>0) for each lead hour (Gamma regression)
- **Expected rain**: `E[RR1] = PoP × μ`

Outputs:
1) Clean evaluation (PR-AUC, ROC-AUC, Brier, LogLoss, Precision/Recall/F1, alarm rate)  
2) A 7-day (168h) forecast table in a **weather-forecast-like** format (0–100% + labels)  
3) Saved models + thresholds under `pointweights/`


In [1]:
pip uninstall -y dask distributed dask-expr

Note: you may need to restart the kernel to use updated packages.


In [ ]:
# ===== 0) Imports & Config =====
import os
import json
import joblib
import numpy as np
import pandas as pd

from sklearn.metrics import (
    average_precision_score,
    roc_auc_score,
    brier_score_loss,
    log_loss,
    precision_recall_curve,
    precision_score,
    recall_score,
    f1_score,
)

SEED = 42
np.random.seed(SEED)

# --- Paths ---
# If you run this notebook elsewhere, change DATA_PATH to your local CSV path.
DATA_PATH = "./H_20_latest-2024-2025.csv"
WEIGHTS_DIR = "point_weights"
os.makedirs(WEIGHTS_DIR, exist_ok=True)

# --- Station & horizon ---
STATION_ID = 20004002
HORIZON = 168  # 7 days * 24h

# --- Columns in your CSV ---
BASE_COLS = ["NUM_POSTE", "AAAAMMJJHH"]
X_COLS = ["RR1", "QRR1", "TD", "QTD", "PMER", "QPMER", "FF", "QFF", "INS", "QINS", "GLO", "QGLO"]

# --- Quality control ---
GOOD_Q_VALUES = {0, 1, 9}

# --- Definitions ---
RAIN_THR = 0.1  # PoP threshold: RR1 >= 0.1 mm/h
CATEGORY_THRESHOLDS = [0.1, 2.5, 7.6, 16.0]  # we will auto-pick what is feasible

# --- Time split (chronological) ---
TRAIN_RATIO = 0.70
VAL_RATIO = 0.15
TEST_RATIO = 0.15

# --- Missing handling ---
FFILL_LIMIT_HOURS = 3

# --- Intensity training guard (rainy samples only) ---
MIN_RAIN_SAMPLES_INTENSITY = 200

pd.set_option("display.max_rows", 200)
pd.set_option("display.max_columns", 200)


In [3]:
# ===== 1) Preprocessing: read -> hourly alignment -> QC -> RAD -> missing handling =====

def read_station_chunked(path: str, station_id: int, usecols: list, chunksize: int = 200_000) -> pd.DataFrame:
    found = []
    for chunk in pd.read_csv(path, sep=";", usecols=usecols, chunksize=chunksize, low_memory=False):
        sub = chunk[chunk["NUM_POSTE"] == station_id]
        if len(sub) > 0:
            found.append(sub)

    if not found:
        raise ValueError(f"No rows found for station {station_id}")

    df = pd.concat(found, axis=0, ignore_index=True)
    df["AAAAMMJJHH"] = df["AAAAMMJJHH"].astype(str).str.zfill(10)
    df["dt"] = pd.to_datetime(df["AAAAMMJJHH"], format="%Y%m%d%H", errors="coerce")
    df = df.dropna(subset=["dt"]).sort_values("dt").reset_index(drop=True)

    print(f"[Read] Station={station_id} rows={len(df)} | dt_min={df['dt'].min()} | dt_max={df['dt'].max()}")
    return df


def ensure_hourly_index(df: pd.DataFrame, station_id: int) -> pd.DataFrame:
    df = df.copy()

    dup = int(df.duplicated("dt").sum())
    if dup > 0:
        numeric_cols = df.select_dtypes(include=[np.number]).columns.tolist()
        non_numeric_cols = [c for c in df.columns if c not in numeric_cols and c != "dt"]
        agg_num = df.groupby("dt")[numeric_cols].mean()
        agg_non = df.groupby("dt")[non_numeric_cols].first() if non_numeric_cols else None
        df = agg_num.join(agg_non, how="left") if agg_non is not None else agg_num
        df = df.reset_index()

    full_idx = pd.date_range(df["dt"].min(), df["dt"].max(), freq="h")
    print(f"[TimeIndex] duplicated={dup} | expected_hours={len(full_idx)} | rows={len(df)} | missing_hours={len(full_idx)-len(df)}")

    df = df.set_index("dt").reindex(full_idx)
    df.index.name = "dt"
    df = df.reset_index()

    df["NUM_POSTE"] = df.get("NUM_POSTE", station_id)
    df["NUM_POSTE"] = df["NUM_POSTE"].ffill().bfill()
    return df


def apply_qc(df: pd.DataFrame, good_q_values=GOOD_Q_VALUES) -> pd.DataFrame:
    df = df.copy()

    for c in ["RR1","TD","PMER","FF","INS","GLO"]:
        if c in df.columns:
            df[c] = pd.to_numeric(df[c], errors="coerce")

    for qc in [c for c in df.columns if c.startswith("Q")]:
        df[qc] = pd.to_numeric(df[qc], errors="coerce").astype("Int64")

    var_q_map = {"RR1":"QRR1","TD":"QTD","PMER":"QPMER","FF":"QFF","INS":"QINS","GLO":"QGLO"}

    for var, qv in var_q_map.items():
        if var in df.columns and qv in df.columns:
            bad_q = ~df[qv].isin(list(good_q_values))
            df.loc[bad_q, var] = np.nan

    def range_clip(var, lo, hi):
        if var not in df.columns:
            return
        bad = (df[var] < lo) | (df[var] > hi)
        df.loc[bad, var] = np.nan

    range_clip("RR1", 0, 200)
    range_clip("TD", -80, 60)
    range_clip("PMER", 850, 1100)
    range_clip("FF", 0, 80)
    range_clip("INS", 0, 60)
    range_clip("GLO", 0, 2000)
    return df


def choose_best_radiation(df: pd.DataFrame, good_q_values=GOOD_Q_VALUES) -> pd.Series:
    candidates = [("GLO","QGLO",(0,2000)), ("INS","QINS",(0,60))]
    scores = []
    for var, qv, (lo, hi) in candidates:
        if var not in df.columns or qv not in df.columns:
            continue
        valid = df[qv].isin(list(good_q_values)) & df[var].notna() & (df[var]>=lo) & (df[var]<=hi)
        valid_rate = float(valid.mean())
        nunique = int(df.loc[valid, var].nunique())
        std = float(df.loc[valid, var].std()) if valid.any() else np.nan
        scores.append((var, valid_rate, nunique, std))
    if not scores:
        print("[RAD] No valid radiation candidate. Using all-NaN RAD.")
        return pd.Series([np.nan]*len(df), index=df.index, name="RAD")

    best = sorted(scores, key=lambda x: (x[1], x[2], x[3]), reverse=True)[0][0]
    print(f"[RAD] Selected radiation feature: {best} | candidates={scores}")
    return df[best].rename("RAD")


def handle_missing_for_features(df: pd.DataFrame, ffill_limit: int = FFILL_LIMIT_HOURS) -> pd.DataFrame:
    df = df.copy()
    base_vars = ["TD", "PMER", "FF", "RAD"]

    for v in base_vars:
        df[f"{v}_isna"] = df[v].isna().astype(int)

    for v in base_vars:
        df[v] = df[v].ffill(limit=ffill_limit)

    return df


# --- run preprocessing ---
if not os.path.exists(DATA_PATH):
    raise FileNotFoundError(f"DATA_PATH not found: {DATA_PATH}")

usecols = BASE_COLS + X_COLS
raw = read_station_chunked(DATA_PATH, STATION_ID, usecols=usecols)
df = ensure_hourly_index(raw, STATION_ID)
df = apply_qc(df)
df["RAD"] = choose_best_radiation(df)
df = handle_missing_for_features(df)

df.head()


[Read] Station=20004002 rows=10516 | dt_min=2024-01-01 00:00:00 | dt_max=2025-03-14 03:00:00
[TimeIndex] duplicated=0 | expected_hours=10516 | rows=10516 | missing_hours=0
[RAD] Selected radiation feature: GLO | candidates=[('GLO', 1.0, 354, 93.04529257264038), ('INS', 1.0, 60, 25.758201159689456)]


dt  NUM_POSTE  AAAAMMJJHH  RR1  QRR1   FF  QFF    TD  QTD  \
0 2024-01-01 00:00:00   20004002  2024010100  0.0     1  2.8    1  10.4    1   
1 2024-01-01 01:00:00   20004002  2024010101  0.0     1  3.0    1   8.9    1   
2 2024-01-01 02:00:00   20004002  2024010102  0.0     1  2.2    1   8.5    1   
3 2024-01-01 03:00:00   20004002  2024010103  0.0     1  1.1    1   7.7    1   
4 2024-01-01 04:00:00   20004002  2024010104  0.0     1  1.3    1   7.6    1   

     PMER  QPMER  GLO  QGLO  INS  QINS  RAD  TD_isna  PMER_isna  FF_isna  \
0  1015.7      1  0.0     9  0.0     9  0.0        0          0        0   
1  1015.5      1  0.0     9  0.0     9  0.0        0          0        0   
2  1015.8      1  0.0     9  0.0     9  0.0        0          0        0   
3  1015.7      1  0.0     9  0.0     9  0.0        0          0        0   
4  1015.9      1  0.0     9  0.0     9  0.0        0          0        0   

   RAD_isna  
0         0  
1         0  
2         0  
3         0  
4         0

In [4]:
# ===== 2) EDA: pick feasible category thresholds (optional "heavy" threshold) =====

def quick_threshold_counts(rr1: pd.Series, thresholds: list) -> dict:
    rr = pd.to_numeric(rr1, errors="coerce")
    counts = {t: int((rr >= t).sum()) for t in thresholds}
    rates  = {t: float((rr >= t).mean()) for t in thresholds}
    return {"counts": counts, "rates": rates}

info = quick_threshold_counts(df["RR1"], CATEGORY_THRESHOLDS)
print("[EDA] counts:", info["counts"])
print("[EDA] rates :", {k: round(v, 6) for k,v in info["rates"].items()})

feasible = [t for t,c in info["counts"].items() if c >= 50]
HEAVY_THR = 2.5 if 2.5 in feasible else None
print(f"[EDA] feasible_thresholds(count>=50): {feasible}")
print(f"[EDA] HEAVY_THR selected: {HEAVY_THR}")


[EDA] counts: {0.1: 505, 2.5: 80, 7.6: 10, 16.0: 0}
[EDA] rates : {0.1: 0.048022, 2.5: 0.007607, 7.6: 0.000951, 16.0: 0.0}
[EDA] feasible_thresholds(count>=50): [0.1, 2.5]
[EDA] HEAVY_THR selected: 2.5


In [5]:
# ===== 3) Feature engineering =====

def add_time_features(df: pd.DataFrame) -> pd.DataFrame:
    df = df.copy()
    dt = df["dt"]
    hour = dt.dt.hour.values
    doy  = dt.dt.dayofyear.values
    df["hour_sin"] = np.sin(2*np.pi*hour/24.0)
    df["hour_cos"] = np.cos(2*np.pi*hour/24.0)
    df["doy_sin"]  = np.sin(2*np.pi*doy/365.25)
    df["doy_cos"]  = np.cos(2*np.pi*doy/365.25)
    df["is_weekend"] = (dt.dt.dayofweek >= 5).astype(int)
    return df


def add_rr_history_features(df: pd.DataFrame, rain_thr=RAIN_THR) -> pd.DataFrame:
    df = df.copy()
    rr1 = pd.to_numeric(df["RR1"], errors="coerce")
    rain_flag = (rr1 >= rain_thr).astype(int)
    df["rain_flag"] = rain_flag

    for lag in [1, 3, 6, 12, 24, 48]:
        df[f"rr1_lag_{lag}"] = rr1.shift(lag)

    df["rr1_sum_6"]  = rr1.rolling(6,  min_periods=1).sum()
    df["rr1_sum_12"] = rr1.rolling(12, min_periods=1).sum()
    df["rr1_sum_24"] = rr1.rolling(24, min_periods=1).sum()

    df["rain_any_24"] = (rain_flag.rolling(24, min_periods=1).max() > 0).astype(int)
    df["rain_any_48"] = (rain_flag.rolling(48, min_periods=1).max() > 0).astype(int)

    # hours since last rain (capped)
    since = np.zeros(len(df), dtype=np.float32)
    cnt = 999.0
    for i, v in enumerate(rain_flag.values):
        cnt = 0.0 if v == 1 else cnt + 1.0
        since[i] = cnt
    df["since_rain_h"] = np.minimum(since, float(HORIZON))
    return df


def add_meteo_roll_features(df: pd.DataFrame) -> pd.DataFrame:
    df = df.copy()
    for v in ["TD", "PMER", "FF", "RAD"]:
        df[f"{v}_mean_6"]  = df[v].rolling(6,  min_periods=1).mean()
        df[f"{v}_mean_24"] = df[v].rolling(24, min_periods=1).mean()
        df[f"{v}_diff_1"]  = df[v].diff(1)
    return df


df_feat = add_time_features(df)
df_feat = add_rr_history_features(df_feat)
df_feat = add_meteo_roll_features(df_feat)

FEATURE_COLS = [
    # time
    "hour_sin","hour_cos","doy_sin","doy_cos","is_weekend",
    # meteo
    "TD","PMER","FF","RAD",
    "TD_mean_6","TD_mean_24","TD_diff_1",
    "PMER_mean_6","PMER_mean_24","PMER_diff_1",
    "FF_mean_6","FF_mean_24","FF_diff_1",
    "RAD_mean_6","RAD_mean_24","RAD_diff_1",
    # missing masks
    "TD_isna","PMER_isna","FF_isna","RAD_isna",
    # RR history
    "rain_flag","rr1_sum_6","rr1_sum_12","rr1_sum_24",
    "rain_any_24","rain_any_48","since_rain_h",
    "rr1_lag_1","rr1_lag_3","rr1_lag_6","rr1_lag_12","rr1_lag_24","rr1_lag_48",
]

X_all = df_feat[FEATURE_COLS].copy()
X_all.tail(3)


hour_sin  hour_cos  doy_sin   doy_cos  is_weekend    TD   PMER   FF  \
10513  0.258819  0.965926  0.95079  0.309835           0   9.7  998.9  2.6   
10514  0.500000  0.866025  0.95079  0.309835           0  11.8  998.2  6.3   
10515  0.707107  0.707107  0.95079  0.309835           0  12.3  997.9  9.2   

       RAD  TD_mean_6  TD_mean_24  TD_diff_1  PMER_mean_6  PMER_mean_24  \
10513  0.0  10.916667   11.029167       -0.9  1000.183333   1000.750000   
10514  0.0  10.950000   11.108333        2.1   999.783333   1000.670833   
10515  0.0  11.116667   11.212500        0.5   999.350000   1000.587500   

       PMER_diff_1  FF_mean_6  FF_mean_24  FF_diff_1  RAD_mean_6  RAD_mean_24  \
10513         -1.2   4.000000    3.783333       -1.3         0.0       59.875   
10514         -0.7   4.733333    3.983333        3.7         0.0       59.875   
10515         -0.3   5.816667    4.166667        2.9         0.0       59.875   

       RAD_diff_1  TD_isna  PMER_isna  FF_isna  RAD_isna  rain_flag  \
10513         0.0        0          0        0         0          1   
10514         0.0        0          0        0         0          0   
10515         0.0        0          0        0         0          0   

       rr1_sum_6  rr1_sum_12  rr1_sum_24  rain_any_24  rain_any_48  \
10513       10.1        10.3        12.3            1            1   
10514       10.1        10.3        12.3            1            1   
10515        7.1        10.3        12.3            1            1   

       since_rain_h  rr1_lag_1  rr1_lag_3  rr1_lag_6  rr1_lag_12  rr1_lag_24  \
10513           0.0        2.2        0.8        0.0         0.0         0.0   
10514           1.0        0.4        3.7        0.0         0.0         0.0   
10515           2.0        0.0        2.2        3.0         0.0         0.0   

       rr1_lag_48  
10513         1.0  
10514         0.0  
10515         0.0

In [6]:
# ===== 4) Labels & chronological split =====

def build_binary_labels(rr1: pd.Series, threshold: float, horizon: int = HORIZON) -> dict:
    labels = {}
    for h in range(1, horizon + 1):
        y_future = rr1.shift(-h)
        y = (y_future >= threshold).astype("float")
        y[y_future.isna()] = np.nan
        labels[h] = y
    return labels


def build_intensity_labels(rr1: pd.Series, horizon: int = HORIZON) -> dict:
    labels = {}
    for h in range(1, horizon + 1):
        y = rr1.shift(-h)
        y = y.where(y > 0, np.nan)  # rainy-only intensity
        labels[h] = y
    return labels


def time_split_indices(n: int, train_ratio=TRAIN_RATIO, val_ratio=VAL_RATIO):
    train_end = int(n * train_ratio)
    val_end   = int(n * (train_ratio + val_ratio))
    idx_train = np.arange(0, train_end)
    idx_val   = np.arange(train_end, val_end)
    idx_test  = np.arange(val_end, n)
    print(f"[Split] train={len(idx_train)} val={len(idx_val)} test={len(idx_test)} (chronological)")
    return idx_train, idx_val, idx_test


rr1 = pd.to_numeric(df_feat["RR1"], errors="coerce")

labels_pop = build_binary_labels(rr1, threshold=RAIN_THR, horizon=HORIZON)
labels_heavy = build_binary_labels(rr1, threshold=HEAVY_THR, horizon=HORIZON) if HEAVY_THR is not None else None
labels_intensity = build_intensity_labels(rr1, horizon=HORIZON)

idx_train, idx_val, idx_test = time_split_indices(len(df_feat))


[Split] train=7361 val=1577 test=1578 (chronological)


In [7]:
# ===== 5) Training (fixed weights): PoP / (optional heavy) / intensity =====

USE_LGBM = True
try:
    import lightgbm as lgb
    from lightgbm import LGBMClassifier, LGBMRegressor
except Exception as e:
    USE_LGBM = False
    print(f"[Model] LightGBM import failed -> fallback to HistGradientBoosting. Error: {e}")

if not USE_LGBM:
    from sklearn.ensemble import HistGradientBoostingClassifier, HistGradientBoostingRegressor


def predict_proba_any(model, X: pd.DataFrame):
    if model is None:
        return None
    if hasattr(model, "predict_proba"):
        return model.predict_proba(X)[:, 1]
    if hasattr(model, "decision_function"):
        z = model.decision_function(X)
        return 1.0 / (1.0 + np.exp(-z))
    return None


def fit_horizon_classifier(X_all, y, idx_train, idx_val):
    y_tr_full = y.iloc[idx_train]
    y_va_full = y.iloc[idx_val]

    tr_mask = ~y_tr_full.isna()
    va_mask = ~y_va_full.isna()

    X_tr = X_all.iloc[idx_train].loc[tr_mask.values]
    y_tr = y_tr_full.loc[tr_mask].astype(int)

    X_va = X_all.iloc[idx_val].loc[va_mask.values]
    y_va = y_va_full.loc[va_mask].astype(int)

    pos = int(y_tr.sum())
    neg = int(len(y_tr) - pos)
    if pos == 0 or len(y_tr) < 200:
        return None, {"pos": pos, "neg": neg, "skipped": True}

    spw = neg / max(pos, 1)

    if USE_LGBM:
        model = LGBMClassifier(
            objective="binary",
            n_estimators=5000,
            learning_rate=0.03,
            num_leaves=31,
            min_child_samples=50,
            subsample=0.8,
            colsample_bytree=0.8,
            reg_lambda=1.0,
            random_state=SEED,
            n_jobs=-1,
            scale_pos_weight=spw,
        )
        model.fit(
            X_tr, y_tr,
            eval_set=[(X_va, y_va)],
            eval_metric="binary_logloss",
            callbacks=[lgb.early_stopping(stopping_rounds=200, verbose=False)]
        )
    else:
        model = HistGradientBoostingClassifier(
            learning_rate=0.05, max_depth=6, max_iter=300, random_state=SEED
        )
        model.fit(X_tr, y_tr)

    return model, {"pos": pos, "neg": neg, "spw": float(spw), "skipped": False}


def fit_horizon_intensity_gamma(X_all, y_rr, idx_train, idx_val, min_pos_samples=MIN_RAIN_SAMPLES_INTENSITY):
    y_tr_full = y_rr.iloc[idx_train]
    y_va_full = y_rr.iloc[idx_val]

    tr_mask = ~y_tr_full.isna()
    va_mask = ~y_va_full.isna()

    n_tr = int(tr_mask.sum())
    n_va = int(va_mask.sum())
    if n_tr < min_pos_samples:
        return None, {"n_train_rain": n_tr, "n_val_rain": n_va, "skipped": True}

    X_tr = X_all.iloc[idx_train].loc[tr_mask.values]
    y_tr = y_tr_full.loc[tr_mask].astype(float)

    X_va = X_all.iloc[idx_val].loc[va_mask.values]
    y_va = y_va_full.loc[va_mask].astype(float)

    if USE_LGBM:
        model = LGBMRegressor(
            objective="gamma",
            n_estimators=5000,
            learning_rate=0.03,
            num_leaves=31,
            min_child_samples=50,
            subsample=0.8,
            colsample_bytree=0.8,
            reg_lambda=1.0,
            random_state=SEED,
            n_jobs=-1,
        )
        model.fit(
            X_tr, y_tr,
            eval_set=[(X_va, y_va)],
            eval_metric="l2",
            callbacks=[lgb.early_stopping(stopping_rounds=200, verbose=False)]
        )
    else:
        model = HistGradientBoostingRegressor(
            learning_rate=0.05, max_depth=6, max_iter=300, random_state=SEED
        )
        model.fit(X_tr, y_tr)

    return model, {"n_train_rain": n_tr, "n_val_rain": n_va, "skipped": False}


# --- Train all horizons (1..168) ---
models_pop, info_pop = {}, {}
models_heavy, info_heavy = ({} , {}) if labels_heavy is not None else (None, None)
models_intensity, info_intensity = {}, {}

print("[Train] PoP models...")
for h in range(1, HORIZON + 1):
    m, info = fit_horizon_classifier(X_all, labels_pop[h], idx_train, idx_val)
    models_pop[h], info_pop[h] = m, info

print("[Train] Heavy models..." if labels_heavy is not None else "[Train] Heavy models: skipped (HEAVY_THR not feasible)")
if labels_heavy is not None:
    for h in range(1, HORIZON + 1):
        m, info = fit_horizon_classifier(X_all, labels_heavy[h], idx_train, idx_val)
        models_heavy[h], info_heavy[h] = m, info

print("[Train] Intensity models...")
for h in range(1, HORIZON + 1):
    m, info = fit_horizon_intensity_gamma(X_all, labels_intensity[h], idx_train, idx_val)
    models_intensity[h], info_intensity[h] = m, info

# quick sanity
print("[Train] Example horizons:")
for h in [1, 24, 72, 168]:
    print(f"  h={h:3d} | PoP skipped={info_pop[h]['skipped']} | Intensity skipped={info_intensity[h]['skipped']}")


[Train] PoP models...
[LightGBM] [Info] Number of positive: 353, number of negative: 7008
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002866 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 4904
[LightGBM] [Info] Number of data points in the train set: 7361, number of used features: 34
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.047955 -> initscore=-2.988340
[LightGBM] [Info] Start training from score -2.988340
[LightGBM] [Info] Number of positive: 353, number of negative: 7008
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003992 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4904
[LightGBM] [Info] Number of data points in the train set: 7361, number of used features: 34
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.047955 -> initscor

In [8]:
# ===== 6) Evaluation (cleaner & more complete) =====

def pick_threshold_best_f1(y_true: np.ndarray, p: np.ndarray) -> float:
    precision, recall, thr = precision_recall_curve(y_true, p)
    if len(thr) == 0:
        return 0.5
    f1 = (2 * precision * recall) / np.maximum(precision + recall, 1e-12)
    f1_thr = f1[:-1]  # align with thr
    best_idx = int(np.nanargmax(f1_thr))
    return float(thr[best_idx])


def eval_classifier_one_h(models: dict, labels: dict, X_all: pd.DataFrame, idx_val, idx_test, h: int):
    # ----- val for threshold -----
    y_val = labels[h].iloc[idx_val]
    mv = ~y_val.isna()
    yv = y_val[mv].astype(int)
    Xv = X_all.iloc[idx_val].loc[mv.values]
    pv = predict_proba_any(models.get(h), Xv) if models.get(h) is not None else None

    if pv is None or len(yv) == 0 or yv.nunique() < 2:
        return None, None

    thr = pick_threshold_best_f1(yv.values, pv)

    # ----- test metrics -----
    y_test = labels[h].iloc[idx_test]
    mt = ~y_test.isna()
    yt = y_test[mt].astype(int)
    Xt = X_all.iloc[idx_test].loc[mt.values]
    pt = predict_proba_any(models[h], Xt)

    pred = (pt >= thr).astype(int)
    out = {
        "h": h,
        "n_test": int(len(yt)),
        "pos_rate_test": float(yt.mean()),
        "thr_val_bestF1": float(thr),
        "pr_auc": float(average_precision_score(yt, pt)) if yt.nunique() > 1 else np.nan,
        "roc_auc": float(roc_auc_score(yt, pt)) if yt.nunique() > 1 else np.nan,
        "brier": float(brier_score_loss(yt, pt)),
        "logloss": float(log_loss(yt, pt, labels=[0,1])),
        "precision@thr": float(precision_score(yt, pred, zero_division=0)),
        "recall@thr": float(recall_score(yt, pred, zero_division=0)),
        "f1@thr": float(f1_score(yt, pred, zero_division=0)),
        "alarm_rate": float(pred.mean()),
    }
    return out, thr


def eval_models(models: dict, labels: dict, X_all: pd.DataFrame, idx_val, idx_test, horizons: list):
    rows = []
    thresholds = {}
    for h in horizons:
        r, thr = eval_classifier_one_h(models, labels, X_all, idx_val, idx_test, h)
        if r is not None:
            rows.append(r)
            thresholds[h] = thr
    dfm = pd.DataFrame(rows).sort_values("h").reset_index(drop=True)
    return dfm, thresholds


KEY_H = [1, 3, 6, 12, 24, 48, 72, 96, 120, 144, 168]
df_eval_pop, thr_pop = eval_models(models_pop, labels_pop, X_all, idx_val, idx_test, KEY_H)
df_eval_pop


h  n_test  pos_rate_test  thr_val_bestF1    pr_auc   roc_auc     brier  \
0     1    1577       0.056436        0.186188  0.410504  0.875766  0.045665   
1     3    1575       0.056508        0.145851  0.270181  0.803870  0.050084   
2     6    1572       0.056616        0.107410  0.161635  0.690985  0.051830   
3    12    1566       0.056833        0.064067  0.187583  0.708873  0.052723   
4    24    1554       0.057272        0.075079  0.084479  0.622714  0.053672   
5    48    1530       0.058170        0.062351  0.073327  0.573135  0.054750   
6    72    1506       0.059097        0.073894  0.086405  0.626069  0.055007   
7    96    1482       0.060054        0.074436  0.070418  0.569396  0.056187   
8   120    1458       0.061043        0.068286  0.077277  0.552183  0.056952   
9   144    1434       0.062064        0.045584  0.097479  0.639305  0.057475   
10  168    1410       0.063121        0.044886  0.052244  0.395695  0.060144   

     logloss  precision@thr  recall@thr    f1@thr  alarm_rate  
0   0.177381       0.429688    0.617978  0.506912    0.081167  
1   0.198266       0.377551    0.415730  0.395722    0.062222  
2   0.205770       0.252747    0.258427  0.255556    0.057888  
3   0.210844       0.110638    0.584270  0.186047    0.300128  
4   0.216504       0.060185    0.146067  0.085246    0.138996  
5   0.221590       0.062500    0.438202  0.109397    0.407843  
6   0.219225       0.098232    0.561798  0.167224    0.337981  
7   0.224705       0.073892    0.505618  0.128940    0.410931  
8   0.226798       0.085271    0.494382  0.145455    0.353909  
9   0.226250       0.062064    1.000000  0.116875    1.000000  
10  0.244051       0.063121    1.000000  0.118746    1.000000

In [9]:
# Evaluate across all horizons (summary + thresholds to save)

all_h = list(range(1, HORIZON + 1))
rows_all = []
thr_pop_all = {}
for h in all_h:
    r, thr = eval_classifier_one_h(models_pop, labels_pop, X_all, idx_val, idx_test, h)
    if r is not None:
        rows_all.append(r)
        thr_pop_all[h] = thr

df_eval_pop_all = pd.DataFrame(rows_all).sort_values("h").reset_index(drop=True)

summary = df_eval_pop_all[["pr_auc","roc_auc","brier","logloss","f1@thr","alarm_rate"]].agg(["mean","median"])
print(summary)

# optional heavy thresholds (if trained)
thr_heavy_all = None
if labels_heavy is not None and models_heavy is not None:
    rows_heavy = []
    thr_heavy_all = {}
    for h in all_h:
        r, thr = eval_classifier_one_h(models_heavy, labels_heavy, X_all, idx_val, idx_test, h)
        if r is not None:
            rows_heavy.append(r)
            thr_heavy_all[h] = thr
    df_eval_heavy_all = pd.DataFrame(rows_heavy).sort_values("h").reset_index(drop=True)
    print("[Heavy] summary:")
    print(df_eval_heavy_all[["pr_auc","brier","logloss","f1@thr"]].agg(["mean","median"]))


          pr_auc   roc_auc     brier   logloss    f1@thr  alarm_rate
mean    0.088346  0.553638  0.055876  0.224446  0.133322    0.483375
median  0.073719  0.571126  0.055937  0.224709  0.119260    0.364070
[Heavy] summary:
          pr_auc     brier   logloss    f1@thr
mean    0.026172  0.015861  0.085181  0.037064
median  0.015395  0.014478  0.083937  0.024525


In [ ]:
# ===== 7) Predict next 7 days (168h) in "forecast-like" format =====

def to_pct(p: float):
    if not np.isfinite(p):
        return np.nan
    return int(np.clip(np.round(p * 100), 0, 100))


def make_forecast_168(
    df_feat: pd.DataFrame,
    X_all: pd.DataFrame,
    models_pop: dict,
    models_intensity: dict,
    models_heavy: dict = None,
    heavy_thr: float = None,
):
    issue_time = df_feat["dt"].iloc[-1]
    x0 = X_all.iloc[[-1]]  # last available feature row

    out = []
    for h in range(1, HORIZON + 1):
        p_pop = np.nan
        if models_pop.get(h) is not None:
            p_pop = float(predict_proba_any(models_pop[h], x0)[0])

        p_heavy = np.nan
        if heavy_thr is not None and models_heavy is not None and models_heavy.get(h) is not None:
            p_heavy = float(predict_proba_any(models_heavy[h], x0)[0])
            # enforce probability consistency: P(>=heavy) <= P(rain)
            if np.isfinite(p_pop) and np.isfinite(p_heavy):
                p_heavy = float(min(p_heavy, p_pop))

        mu = np.nan
        if models_intensity.get(h) is not None:
            mu = float(models_intensity[h].predict(x0)[0])

        e_rr = np.nan
        if np.isfinite(p_pop) and np.isfinite(mu):
            e_rr = p_pop * mu

        # "official-like" label (for this dry station: robustly do 3 bins)
        # - if PoP < 20% => "no rain" (dominant)
        # - else if heavy prob available and >=20% => "medium rain or heavier"
        # - else => "small rain"
        if not np.isfinite(p_pop):
            label = "Unknown"
        elif p_pop < 0.20:
            label = "no rain"
        else:
            if heavy_thr is not None and np.isfinite(p_heavy) and p_heavy >= 0.20:
                label = f"medium rain or heavier (≥{heavy_thr}mm/h)"
            else:
                label = "small rain"

        out.append({
            "issue_time": issue_time,
            "valid_time": issue_time + pd.Timedelta(hours=h),
            "lead_h": h,
            "PoP": p_pop,
            "PoP_%": to_pct(p_pop),
            (f"P_RR>={heavy_thr}" if heavy_thr is not None else "P_heavy"): p_heavy,
            "mu_RR_given_rain": mu,
            "E_RR_mm_per_h": e_rr,
            "label": label,
        })

    fc = pd.DataFrame(out)
    print(f"[Forecast] issue_time={issue_time} | generated {len(fc)} rows (1..{HORIZON}h)")
    return fc


forecast_168 = make_forecast_168(
    df_feat=df_feat,
    X_all=X_all,
    models_pop=models_pop,
    models_intensity=models_intensity,
    models_heavy=models_heavy,
    heavy_thr=HEAVY_THR,
)

forecast_168.head(48)


[Forecast] issue_time=2025-03-14 03:00:00 | generated 168 rows (1..168h)


issue_time          valid_time  lead_h       PoP  PoP_%  \
0  2025-03-14 03:00:00 2025-03-14 04:00:00       1  0.191739     19   
1  2025-03-14 03:00:00 2025-03-14 05:00:00       2  0.153921     15   
2  2025-03-14 03:00:00 2025-03-14 06:00:00       3  0.156843     16   
3  2025-03-14 03:00:00 2025-03-14 07:00:00       4  0.133856     13   
4  2025-03-14 03:00:00 2025-03-14 08:00:00       5  0.133408     13   
5  2025-03-14 03:00:00 2025-03-14 09:00:00       6  0.107410     11   
6  2025-03-14 03:00:00 2025-03-14 10:00:00       7  0.107700     11   
7  2025-03-14 03:00:00 2025-03-14 11:00:00       8  0.079823      8   
8  2025-03-14 03:00:00 2025-03-14 12:00:00       9  0.079243      8   
9  2025-03-14 03:00:00 2025-03-14 13:00:00      10  0.079753      8   
10 2025-03-14 03:00:00 2025-03-14 14:00:00      11  0.079718      8   
11 2025-03-14 03:00:00 2025-03-14 15:00:00      12  0.079533      8   
12 2025-03-14 03:00:00 2025-03-14 16:00:00      13  0.079404      8   
13 2025-03-14 03:00:00 2025-03-14 17:00:00      14  0.079404      8   
14 2025-03-14 03:00:00 2025-03-14 18:00:00      15  0.050751      5   
15 2025-03-14 03:00:00 2025-03-14 19:00:00      16  0.046730      5   
16 2025-03-14 03:00:00 2025-03-14 20:00:00      17  0.073977      7   
17 2025-03-14 03:00:00 2025-03-14 21:00:00      18  0.062560      6   
18 2025-03-14 03:00:00 2025-03-14 22:00:00      19  0.046772      5   
19 2025-03-14 03:00:00 2025-03-14 23:00:00      20  0.046669      5   
20 2025-03-14 03:00:00 2025-03-15 00:00:00      21  0.046647      5   
21 2025-03-14 03:00:00 2025-03-15 01:00:00      22  0.046804      5   
22 2025-03-14 03:00:00 2025-03-15 02:00:00      23  0.058416      6   
23 2025-03-14 03:00:00 2025-03-15 03:00:00      24  0.048348      5   
24 2025-03-14 03:00:00 2025-03-15 04:00:00      25  0.046645      5   
25 2025-03-14 03:00:00 2025-03-15 05:00:00      26  0.048348      5   
26 2025-03-14 03:00:00 2025-03-15 06:00:00      27  0.048348      5   
27 2025-03-14 03:00:00 2025-03-15 07:00:00      28  0.046654      5   
28 2025-03-14 03:00:00 2025-03-15 08:00:00      29  0.046787      5   
29 2025-03-14 03:00:00 2025-03-15 09:00:00      30  0.046704      5   
30 2025-03-14 03:00:00 2025-03-15 10:00:00      31  0.046723      5   
31 2025-03-14 03:00:00 2025-03-15 11:00:00      32  0.069071      7   
32 2025-03-14 03:00:00 2025-03-15 12:00:00      33  0.046742      5   
33 2025-03-14 03:00:00 2025-03-15 13:00:00      34  0.046736      5   
34 2025-03-14 03:00:00 2025-03-15 14:00:00      35  0.077254      8   
35 2025-03-14 03:00:00 2025-03-15 15:00:00      36  0.048634      5   
36 2025-03-14 03:00:00 2025-03-15 16:00:00      37  0.046842      5   
37 2025-03-14 03:00:00 2025-03-15 17:00:00      38  0.061720      6   
38 2025-03-14 03:00:00 2025-03-15 18:00:00      39  0.046851      5   
39 2025-03-14 03:00:00 2025-03-15 19:00:00      40  0.046698      5   
40 2025-03-14 03:00:00 2025-03-15 20:00:00      41  0.065662      7   
41 2025-03-14 03:00:00 2025-03-15 21:00:00      42  0.052309      5   
42 2025-03-14 03:00:00 2025-03-15 22:00:00      43  0.052886      5   
43 2025-03-14 03:00:00 2025-03-15 23:00:00      44  0.049175      5   
44 2025-03-14 03:00:00 2025-03-16 00:00:00      45  0.049187      5   
45 2025-03-14 03:00:00 2025-03-16 01:00:00      46  0.049226      5   
46 2025-03-14 03:00:00 2025-03-16 02:00:00      47  0.055003      6   
47 2025-03-14 03:00:00 2025-03-16 03:00:00      48  0.051307      5   

    P_RR>=2.5  mu_RR_given_rain  E_RR_mm_per_h label  
0    0.001880          1.229180       0.235682    无雨  
1    0.153921          1.308505       0.201406    无雨  
2    0.074792          1.285923       0.201688    无雨  
3    0.033295          1.293763       0.173178    无雨  
4    0.043317          1.298575       0.173240    无雨  
5    0.013089          1.296331       0.139239    无雨  
6    0.006811          1.296265       0.139607    无雨  
7    0.008798          1.254745       0.100157    无雨  
8    0.079243          1.235835      

In [11]:
# ===== 8) Save fixed weights + thresholds to pointweights/ =====

bundle = {
    "station_id": STATION_ID,
    "horizon": HORIZON,
    "rain_thr": RAIN_THR,
    "heavy_thr": HEAVY_THR,
    "feature_cols": FEATURE_COLS,
    "models_pop": models_pop,
    "models_heavy": models_heavy,
    "models_intensity": models_intensity,
    "thresholds_pop": thr_pop_all,          # per-h threshold (picked on val, best F1)
    "thresholds_heavy": thr_heavy_all,      # None if not trained
    "train_info": {
        "pop": info_pop,
        "heavy": info_heavy,
        "intensity": info_intensity,
    },
}

out_path = os.path.join(WEIGHTS_DIR, f"rain_station{STATION_ID}_h{HORIZON}_bundle.joblib")
joblib.dump(bundle, out_path)
print("[Save] bundle ->", out_path)


[Save] bundle -> pointweights\rain_station20004002_h168_bundle.joblib


In [12]:
# (Optional) Quick load test

loaded = joblib.load(os.path.join(WEIGHTS_DIR, f"rain_station{STATION_ID}_h{HORIZON}_bundle.joblib"))
print("[Load] keys:", list(loaded.keys()))
print("[Load] station_id:", loaded["station_id"], "| horizon:", loaded["horizon"], "| heavy_thr:", loaded["heavy_thr"])


[Load] keys: ['station_id', 'horizon', 'rain_thr', 'heavy_thr', 'feature_cols', 'models_pop', 'models_heavy', 'models_intensity', 'thresholds_pop', 'thresholds_heavy', 'train_info']
[Load] station_id: 20004002 | horizon: 168 | heavy_thr: 2.5
